In [1]:
import folium
folium_map = folium.Map(location=[40.738, -73.98],
                        zoom_start=13,
                        tiles="CartoDB dark_matter")

marker = folium.CircleMarker(location=[40.738, -73.98])
marker.add_to(folium_map)

In [2]:
folium_map

In [3]:
import pandas as pd

bike_data = pd.read_csv("201610-citibike-tripdata.csv")

bike_data["Start Time"] = pd.to_datetime(bike_data["Start Time"])
bike_data["Stop Time"] = pd.to_datetime(bike_data["Stop Time"])
bike_data["hour"] = bike_data["Start Time"].map(lambda x: x.hour)

In [4]:
bike_data.head()

Trip Duration          Start Time           Stop Time  Start Station ID  \
0            328 2016-10-01 00:00:07 2016-10-01 00:05:35               471   
1            398 2016-10-01 00:00:11 2016-10-01 00:06:49              3147   
2            430 2016-10-01 00:00:14 2016-10-01 00:07:25               345   
3            351 2016-10-01 00:00:21 2016-10-01 00:06:12              3307   
4           2693 2016-10-01 00:00:21 2016-10-01 00:45:15              3428   

        Start Station Name  Start Station Latitude  Start Station Longitude  \
0  Grand St & Havemeyer St               40.712868               -73.956981   
1          E 85 St & 3 Ave               40.778012               -73.954071   
2          W 13 St & 6 Ave               40.736494               -73.997044   
3   West End Ave & W 94 St               40.794165               -73.974124   
4          8 Ave & W 16 St               40.740983               -74.001702   

   End Station ID              End Station Name  End Station Latitude  \
0            3077          Stagg St & Union Ave             40.708771   
1            3140               1 Ave & E 78 St             40.771404   
2             470               W 20 St & 8 Ave             40.743453   
3            3357      W 106 St & Amsterdam Ave             40.800836   
4            3323  W 106 St & Central Park West             40.798186   

   End Station Longitude  Bike ID   User Type  Birth Year  Gender  hour  
0             -73.950953    25254  Subscriber      1992.0       1     0  
1             -73.953517    17810  Subscriber      1988.0       2     0  
2             -74.000040    20940  Subscriber      1965.0       1     0  
3             -73.966449    19086  Subscriber      1993.0       1     0  
4             -73.960591    26502  Subscriber      1991.0       1     0

In [5]:
# select the first occurrence of each station id
locations = bike_data.groupby("Start Station ID").first()

# and select only the tree columns we are interested in
locations = locations.loc[:, ["Start Station Latitude",
                              "Start Station Longitude",
                              "Start Station Name"]]

In [6]:
subset = bike_data[bike_data["hour"]==18]

In [7]:
departure_counts =  subset.groupby("Start Station ID").count()

# select one column
departure_counts = departure_counts.iloc[:,[0]]

# and rename that column
departure_counts.columns= ["Departure Count"]

In [8]:
arrival_counts =  subset.groupby("End Station ID").count()

# select one column
arrival_counts = arrival_counts.iloc[:,[0]]

# and rename that column
arrival_counts.columns= ["Arrival Count"]

In [9]:
trip_counts = departure_counts.join(locations).join(arrival_counts)

In [10]:
for index, row in trip_counts.iterrows():
    net_departures = (row["Departure Count"]-row["Arrival Count"])
    radius = net_departures/20
    if net_departures>0:
        color="#E37222" # tangerine
    else:
        color="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["Start Station Latitude"],
                                  row["Start Station Longitude"]),
                        radius=radius,
                        color=color,
                        fill=True).add_to(folium_map)

In [11]:
folium_map